# 3次元形態処理

## A. (物理)オブジェクト処理

### A.1 物理オブジェクトのデータの持たせ方

- 計算空間内のすべてのオブジェクト(pythonでいうオブジェクトではなく。計算空間内に設定した「物理」オブジェクトのこと)は、すべて`ID`で表し、その属性は`ID`を$key$とする辞書として管理する。


- `ID`の暫定設定
  - $0～9999$: 地表面, 天空面
  - $10000～19999$: 空間, 空気, 気体, 物体のないスペース
  - $20000～99999$: 物体のフレーム
  - $100000～999999$: 物体の表面(大きいものから微細に分割したものまで)
  

- 括り毎にIDリストがあるといいかも。いらないかもしれないが。


### A.2 所属関係

- $ParentObj[ID]$: そのオブジェクトが属する「親」の$ID$
- $ChilObj[ID]$: そのオブジェクトに属する「子」の$ID$リスト
- $ObjName[ID]$: オブジェクトの名前(存在確認も兼ねるので必須。ユニークな名前としたい)。


### A.3 形態データ

- オブジェクトの頂点位置
  - $Point[ID] = [P_0, P_1, P_2, …, P_{N-1}]$
  - $P_i$ には、各点の座標リスト $[x_i, y_i, z_i]$ が入る
  - 【多面体】頂点の並びは任意→(以下予定)平面の取り出しを自動化→各表面は子オブジェクトとして登録。
    - ただし、「凹んだ」形状は取り出せないので、分割して登録する等の対応が必要。    
  - 【平面多角形】$[P_0, P_1, P_2, …, P_{N-1}]$ の並びは、法線ベクトルを右ねじの法則の「親指」としたときに回す順番とする。
  - 【円】？？？
  - 【球】？？？？


- 【平面多角形の場合】平面の式 $ax+by+cz=d$ の係数: 
  - $PlaneEq[ID] = [a, b, c, d]$ 
  - $PlaneEq[ID][0:3] = [a, b, c]$ が法線ベクトル。大きさは$1$。  
    → 法線ベクトルの向きはその表面から接する空間に向かう向き
    
    
- $CenterP[ID] = [x, y, z]$ : 重心位置等そのオブジェクトを代表する点の座標  
  - 厳密に重心である必要はない。計算が簡単な座標でよい
  
  
- $NearP[ID] = [x, y, z]$ : オブジェクトの中で最も原点よりの点の座標
  - 頂点座標とは限らない。
  - 厳密な値である必要はない(??)
    

### A.4 属性

- $ObjType[ID]$: オブジェクトの形状
  - 【立体】板状, 直方体, 多面体, …… (??)
  - 【表面】三角形, 四角形, 長方形, 多角形, …… (??)
  - そもそも必要かどうか要検討
  
  
- $Area[ID]$:【平面多角形の場合】オブジェクトの面積$\;[m^2]$


- $Volume[ID]$:【立体の場合】オブジェクトの体積$\;[m^3]$

### A.999 備忘

- 空間との所属関係 → 大本はIDで分類? → 表面には所属関係を持たせる


- 日射計算、伝熱計算する、しないの識別値


- 時系列データの持たせ方    
  - 取得日射量、空間温度、表面温度、エネルギー消費量
  - 伝熱計算の「裏側」の持たせ方
    - 裏側の温度等条件の持たせ方


- 短波長、長波長の透過、吸収、反射率
  - モードの違いの反映(季節間, 時間帯)
  - 入射角特性
  - 指向性(鏡面反射, 完全拡散反射)
  
  
- 日射計算 → 伝熱計算 → 暖冷房(空調)エネルギー計算
  - 時間進行
  - 手順
  
  
- 表面間の関係
  - 形態係数
  - 日射受照の持たせ方

## B. 空間基本処理

### B.1 基本演算


- $\vec{a}=(x_a, y_a, z_a)$, $\vec{b}=(x_b, y_b, z_b)$ の外積 $\vec{a} \times \vec{b}=(y_a z_b - z_a y_b, \; z_a x_b - x_a z_b, \; x_a y_b - y_a x_b )$
  - $|\vec{a} \times \vec{b}| = |\vec{a}||\vec{b}| \sin \theta$
- $\vec{a}=(x_a, y_a, z_a)$, $\vec{b}=(x_b, y_b, z_b)$ の内積 $\vec{a} \vec{b}= x_a x_b + y_a y_b + z_a z_b = |\vec{a}||\vec{b}| \cos \theta$
- 点$(x_0,y_0,z_0)$から、平面$ax+by+cz=d$までの距離：$l=\dfrac{ \bigl| \: ax_0+by_0+cz_0-d \: \bigr| }{ \sqrt{a^2+b^2+c^2} }$  
http://w3e.kanazawa-it.ac.jp/math/category/kika/zutohouteisiki/henkan-tex.cgi?target=/math/category/kika/zutohouteisiki/suisen-no-nagasa-2.html

In [1]:
import numpy as np

""" ベクトルのスカラー倍 """
def calc_scalar_times_vector(VectorA00, ra):
    
    scalar_times_vector = [ VectorA00[0] * ra, VectorA00[1] * ra, VectorA00[2] * ra ]
    
    return scalar_times_vector


""" 倍率考慮のベクトル和 """
def calc_sum_vector(VectorA00, ra, VectorB00, rb):
    
    sum_vector = [ VectorA00[0] * ra + VectorB00[0] * rb
                  ,VectorA00[1] * ra + VectorB00[1] * rb
                  ,VectorA00[2] * ra + VectorB00[2] * rb ]
    
    return sum_vector


""" A×B の外積計算 """
def calc_vector_product(VectorA00, VectorB00):
    # 大きさが |A||B|sinθ で、向きがベクトルAからBに回したときの右ねじの方向となるベクトルを算出

    Vector_product = [0 for j in range(3)]
    
    Vector_product = [ VectorA00[1] * VectorB00[2] - VectorA00[2] * VectorB00[1] 
                      ,VectorA00[2] * VectorB00[0] - VectorA00[0] * VectorB00[2] 
                      ,VectorA00[0] * VectorB00[1] - VectorA00[1] * VectorB00[0] ]
    
    return Vector_product


""" A･Bの内積計算 """
def calc_scalar_product(VectorA00, VectorB00):
    # スカラーで |A||B|cosθ を出力
    
    Scalar_product = VectorA00[0] * VectorB00[0] + VectorA00[1] * VectorB00[1] + VectorA00[2] * VectorB00[2]
    
    return Scalar_product


""" ベクトルの大きさ """
def calc_mag_vector(VectorA00):
    
    mag_Vector = ( VectorA00[0]**2 + VectorA00[1]**2 + VectorA00[2]**2 ) **0.5
    
    return mag_Vector


""" 空間3点の座標から平面の方程式を作成 """
def calc_plane_eq(PointA, PointB, PointC):
    # 平面の式：ax+by+cz=d      → Plane_Eq[0]x+Plane_Eq[1]y+Plane_Eq[2]z=Plane_Eq[3] 
    
    VectorBA = calc_sum_vector(PointA, 1.0, PointB, -1.0)   # 点B→Aのベクトル
    VectorCA = calc_sum_vector(PointA, 1.0, PointC, -1.0)   # 点C→Aのベクトル
    Plane_Eq = calc_vector_product(VectorBA, VectorCA)         # 外積で法線ベクトルを作成
    Plane_Eq = calc_scalar_times_vector( Plane_Eq, 1.0 / calc_mag_vector(Plane_Eq) )
                                                            # 平面の法線ベクトルの大きさ|n|=1に基準化
    Plane_Eq.append( calc_scalar_product(Plane_Eq, PointA) )      # 右辺定数項をPlane_Eq[3]として付加
    
    return Plane_Eq


""" PointAから平面に下ろした垂線の長さ(距離)の算出 """
def calc_length_point_to_plane(PointA, Plane_Eq):
    
    Length_point_to_plane = ( abs(calc_scalar_product(PointA, Plane_Eq[0:3]) - Plane_Eq[3]) 
                          / calc_mag_vector(Plane_Eq[0:3]) )
    
    return Length_point_to_plane


In [4]:
""" calc_vector_product - Test """
VectorA00 = [1,0,0]
VectorB00 = [0,1,0]
Vector_product = calc_vector_product(VectorA00, VectorB00)
print(Vector_product)

""" calc_plane_eq - Test """
PointA = [0,1,1]
PointB = [1,2,3]
PointC = [2,4,1]

PointA = [0,0,0]
PointB = [1,0,0]
PointC = [0,1,0]
Plane_Eq = calc_plane_eq(PointA, PointB, PointC)
print(Plane_Eq, calc_scalar_product(Plane_Eq[0:3], PointA)-Plane_Eq[3]
              , calc_scalar_product(Plane_Eq[0:3], PointB)-Plane_Eq[3]
              , calc_scalar_product(Plane_Eq[0:3], PointC)-Plane_Eq[3] )

""" calc_length_point_to_plane - Test """
Plane_Eq = [1,2,3,4]
PointA = [7,2,1]
Length_point_to_plane = calc_length_point_to_plane(PointA, Plane_Eq)

[TF, Point] = calc_intersection(Plane_Eq, PointA, Plane_Eq[0:3])
mag_Vector = calc_mag_vector( calc_sum_vector(Point, 1.0, PointA, -1.0) )  
print(Length_point_to_plane, mag_Vector, Length_point_to_plane - mag_Vector)

[0, 0, 1]
[0.0, 0.0, 1.0, 0.0] 0.0 0.0 0.0
2.6726124191242437 2.6726124191242437 0.0


### B.2 平面と線分の交点

http://www.hiramine.com/programming/graphics/3d_planesegmentintersection.html より

- 平面の式：$ax+by+cz=d$,  直線の基点：$(x_0, y_0, z_0)$,  直線の方向ベクトル：$(x_1, y_1, z_1)$


- $ax_1 + by_1 + cz_1 = 0$の場合は、平面と直線が平行→交点なし
- $ax_1 + by_1 + cz_1 \neq 0$の場合は、$t = \{ d - ( ax_0 + by_0 + cz_0 ) \} \big/ ( ax_1 + by_1 + cz_1 ) $を媒介として、交点の座標は $(x_2, y_2, z_2) = (x_0, y_0, z_0) + (x_1, y_1, z_1) \times t $ となる。


In [3]:
""" 基点と方向ベクトルからなる直線と平面の交点の座標を求める """
def calc_intersection(Plane_Eq, PointB, Vector):
    # 平面の式：ax+by+cz=d      → Plane_Eq[0]x+Plane_Eq[1]y+Plane_Eq[2]z=Plane_Eq[3] 
    # 直線:基点の座標(x0,y0,z0) → (PointB[0],PointB[1],PointB[2])
    # 方向ベクトル(x1,y1,z1)    → (Vector[0],Vector[1],Vector[2])
    
    Point = [0,0,0]
    Den = calc_scalar_product(Plane_Eq, Vector)
    
    if Den == 0:
        TF = False    # 方向ベクトルが平面と平行 → 交わらない
    else:
        TF = True     # 方向ベクトルが平面と平行でない → 交わる
        t = ( Plane_Eq[3] - calc_scalar_product(Plane_Eq, PointB) ) / Den
            # tは方向ベクトルの倍率 → 基点からスタートして交点に到達するまでの
        Point = calc_sum_vector(PointB, 1.0, Vector, t)
    
    return [TF, Point]


In [5]:
""" calc_intersection - Test """

Plane_Eq = [1,1,1,1]
PointB = [0,0,0]
Vector = [1,1,-1]
[TF, Point] = calc_intersection(Plane_Eq, PointB, Vector)
print(TF,Point)

True [1.0, 1.0, -1.0]



### B.3 多角形とその平面上の点の内外判定

- 多角形の各頂点と判定する点が厳密に同一平面上になくても(だいたい)判断できるはず

http://www.endo-yuta.com/2011/09/blog-post_06.html より
- ただし、上記html中で、外積の計算がベクトルになっていない点がおかしい(??) 
  - 外積と法線ベクトルの内積の符号で判断、に修正して以下が設定と手順。 
  
  
- 設定 
  - $N$角形の頂点の座標：$(x_0, y_0, z_0)$, $(x_1, y_1, z_1)$, …, $(x_{N-1}, y_{N-1}, z_{N-1})$
  - 判定する点の座標：$(x, y, z)$
- 計算手順
  - 頂点$0$から判定する点へのベクトル $(x - x_0, \; y - y_0, \; z - z_0)$ と 頂点$1$から判定する点へのベクトル $(x - x_1, \; y - y_1, \; z - z_1)$ の外積 $(x - x_0, \; y - y_0, \; z - z_0) \times (x - x_1, \; y - y_1, \; z - z_1)$ から法線ベクトルを決定  
      
    → $\vec{n} = \dfrac{(x - x_0, \; y - y_0, \; z - z_0) \times (x - x_1, \; y - y_1, \; z - z_1)}{ \bigl|(x - x_0, \; y - y_0, \; z - z_0) \times (x - x_1, \; y - y_1, \; z - z_1) \bigr| } $  
      
    → $\vec{n}$ は、$N$角形の頂点による右ねじの法則の向き
  - 頂点$i$→判定する点のベクトル: $(x - x_i, \; y - y_i, \; z - z_i)$
  - 頂点$i$→$i+1$のベクトル: $(x_{i+1} - x_i, \; y_{i+1} - y_i, \; z_{i+1} - z_i)$

  - 上の$2$つのベクトルの外積 $(x - x_i, \; y - y_i, \; z - z_i) \times (x_{i+1} - x_i, \; y_{i+1} - y_i, \; z_{i+1} - z_i)$ と法線ベクトル$\vec{n}$の内積(スカラー)をとり、その符号を確認する。  
  → $0$の場合は、判定する点はその辺上  
  - すべての辺のベクトルについて確認して、すべて同じ符号となれば、判定する点は$N$角形の内側となる。

In [6]:
import numpy as np

""" ある平面上の点がその平面上の多角形の「中」にあるかどうかを判定 """
def inside_or_not(PointA, PointB):
    # PointA: 判定する点の座標 → PointA[0], PointA[1], PointA[2])
    # PointB: N角形の頂点の座標 → PointB[0], PointB[1], …, PointB[N-1]
    # PointB[i]の座標は → PointB[i][0], PointB[i][1], PointB[i][2]

    VectorA = [0 for j in range(3)]
    VectorB = [0 for j in range(3)]
    ScalarC_pm = [0 for i in range(2)]
    inside = True

    VectorN = calc_plane_eq(PointA, PointB[0], PointB[1])[0:3]
       # 平面の方程式の係数から法線ベクトルを抽出
    
    for i in range(len(PointB)):
        VectorA = calc_sum_vector(PointA, 1, PointB[i], -1)
        if i != len(PointB) - 1:
            VectorB = calc_sum_vector(PointB[i+1], 1, PointB[i], -1)
        elif i == len(PointB) - 1:
            VectorB = calc_sum_vector(PointB[0], 1, PointB[i], -1)
        ScalarC = calc_scalar_product( VectorN, calc_vector_product(VectorA, VectorB) )
            # ベクトルA×ベクトルBのベクトルと法線ベクトルの内積をとり「向き」を確認
        if ScalarC > 0:
            ScalarC_pm[1] += ScalarC    # 向きが正のものを積算
        elif ScalarC < 0:
            ScalarC_pm[0] += ScalarC    # 向きが負のものを積算
        if ScalarC_pm[0] * ScalarC_pm[1] != 0: 
            inside = False              # 向きが揃っていない → その点は多角形の外にあると判定
            # break  # テスト中はbreak文は切る
            
    return [inside, ScalarC_pm]


In [7]:
""" inside_or_not - Test """

PointA = [0,0,0]
PointB = [[1,1,0],[-1,1,0],[-1,-1,0],[1,-1,0]]
[inside, ScalarC_pm] = inside_or_not(PointA, PointB)
print(inside, ScalarC_pm)

# \確認1.xlsx "inside_or_not"シート → \inside_or_not.csv を作成 → \TestConfigPS 下に置いて読み込み → 計算

import pandas as pd
import sys
csv_input = pd.read_csv(filepath_or_buffer="./TestConfigPS/inside_or_not.csv", encoding="ms932", sep=",")
if csv_input.columns[0]!="inside_or_not":
    sys.exit("ファイル内に貼り付けたテスト条件が違います")
for i in range(len(csv_input)):
    #inside_or_not,xa,ya,za,xb0,yb0,zb0,xb1,yb1,zb1,xb2,yb2,zb2,xb3,yb3,zb3,Cscalar_pm0,Cscalar_pm1,insideA
    case = csv_input.values[i][0]
    PointA = csv_input.values[i][1:4]
    ScalarC_pmA = csv_input.values[i][-3:-1]
    insideA = csv_input.values[i][-1]
    for j in range(int(len(csv_input.values[i][4:-3])/3)):
        PointB[j] = csv_input.values[i][4+3*j:4+3*j+3]
    [inside, ScalarC_pm] = inside_or_not(PointA, PointB)
    insideB =  "T" if inside  == True else "N"
    insideB += "T" if insideA == True else "N"
    insideB += "●●●●●●" if inside != insideA else ""
    print('case = {}: inside = {}, ScalarC_m = {}, 期待値 = {}, 残差 = {}, ScalarC_p = {}, 期待値 = {}, 残差 = {}'
          .format( case, insideB, ScalarC_pm[0], ScalarC_pmA[0], ScalarC_pm[0] - ScalarC_pmA[0]
                                , ScalarC_pm[1], ScalarC_pmA[1], ScalarC_pm[1] - ScalarC_pmA[1] ))
    

True [-8.0, 0]
case = 1: inside = TT, ScalarC_m = -8.0, 期待値 = -8.0, 残差 = 0.0, ScalarC_p = 0, 期待値 = 0.0, 残差 = 0.0
case = 2: inside = TT, ScalarC_m = -13.844, 期待値 = -13.844000000000001, 残差 = 1.7763568394002505e-15, ScalarC_p = 0, 期待値 = 0.0, 残差 = 0.0
case = 3: inside = TT, ScalarC_m = -19.982092816652845, 期待値 = -19.982092816652898, 残差 = 5.3290705182007514e-14, ScalarC_p = 0, 期待値 = 0.0, 残差 = 0.0
case = 4: inside = TT, ScalarC_m = -30.95612508050729, 期待値 = -30.956125080507103, 残差 = -1.8829382497642655e-13, ScalarC_p = 0, 期待値 = 0.0, 残差 = 0.0
case = 5: inside = NN, ScalarC_m = -20.144472579862466, 期待値 = -20.144472579862498, 残差 = 3.197442310920451e-14, ScalarC_p = 0.16237976320962147, 期待値 = 0.162379763209581, 残差 = 4.0467629247586956e-14
case = 6: inside = NN, ScalarC_m = -31.207682727975993, 期待値 = -31.2076827279758, 残差 = -1.9184653865522705e-13, ScalarC_p = 0.25155764746870796, 期待値 = 0.251557647468729, 残差 = -2.1038726316646716e-14
case = 7: inside = NT●●●●●●, ScalarC_m = -19.982092816652877, 期


### B.4 多角形の面積

- 2ベクトルからなる平行四辺形の面積は外積の大きさ → 2ベクトルでできる三角形の面積はその半分
- 多角形の1つの頂点から他の点へのベクトルで、多角形を三角形に分割 → それぞれの面積の和で算定。

In [8]:
""" ある平面上の多角形の面積 """
def calc_area_of_polygon(PointB):
    # PointB: N角形の頂点の座標 → PointB[0], PointB[1], …, PointB[N-1]
    # PointB[i]の座標は → PointB[i][0], PointB[i][1], PointB[i][2]
    
    Area_of_Polygon = 0    
    for i in range(1, len(PointB)-1):
        VectorA = calc_sum_vector(PointB[i],   1, PointB[0], -1)
        VectorB = calc_sum_vector(PointB[i+1], 1, PointB[0], -1)        
        Area_of_Polygon += calc_mag_vector( calc_vector_product(VectorA, VectorB) ) / 2
    
    return Area_of_Polygon


In [9]:
""" calc_area_of_polygon - Test """

PointB = [[1,1,0],[-1,1,0],[-1,-1,-2],[1,-1,-2]]
Area_of_Polygon = calc_area_of_polygon(PointB)
print(Area_of_Polygon, 4*2**0.5)

5.656854249492381 5.656854249492381


## C. 平面(多角形)オブジェクト表面から半球に投射(?)して衝突判定



### C.1 任意の平面上で点$A$から半径$r$、角度$\theta$の位置にある点の座標を計算する方法

$N$角形がある平面上において、平面上の点$A$から半径 $r$ 離れて、角度 $\theta$ まわした平面上の点$P$の座標を計算する。

- $r = |\vec{AP}|$ となる点$P$を求める
- 角度 $\theta \; [rad]$ の起点は点$A$から頂点$B_0$に向かうベクトルとする → $\vec{AB_0}=(x_{b0}-x_a, y_{b0}-y_a, z_{b0}-z_a)$  
    → 平面上で頂点$0$から頂点$N$へまわる方向に $\theta$ が増えることとする$(0～2\pi)$。
- 点$A$起点の平面上の点$P$を、$\vec{AB_0}$、$\vec{AB_1}$を使用して表す: $\vec{OP} = \vec{OA} + \vec{AP} = \vec{OA} + s \vec{AB_0} + t \vec{AB_1}   \qquad (1) $
- 点$A$と点$P$の距離: $|\vec{AP}|^2 = |s \vec{AB_0} + t \vec{AB_1}|^2 = (s \vec{AB_0} + t \vec{AB_1})･(s \vec{AB_0} + t \vec{AB_1}) = s^2 |\vec{AB_0}|^2 + 2st \vec{AB_0}･\vec{AB_1} + t^2 |\vec{AB_1}|^2 = r^2  \qquad (2) $
- $\vec{AB_0}$ と $\vec{AP}$ の内積より → $ r |\vec{AB_0}| \cos \theta = \vec{AB_0}･\vec{AP} = \vec{AB_0}･(s \vec{AB_0} + t \vec{AB_1}) = s |\vec{AB_0}|^2 + t \vec{AB_0}･\vec{AB_1}$  
    → $s = ( r |\vec{AB_0}| \cos \theta - t \vec{AB_0}･\vec{AB_1} ) \; \big/ \; |\vec{AB_0}|^2 \qquad (3) $
- 式$(3)$を式$(2)$に代入  
    →$( r |\vec{AB_0}| \cos \theta - t \vec{AB_0}･\vec{AB_1} )^2 + 2( r |\vec{AB_0}| \cos \theta - t \vec{AB_0}･\vec{AB_1} )t \vec{AB_0}･\vec{AB_1} + t^2 |\vec{AB_0}|^2 |\vec{AB_1}|^2 = r^2 |\vec{AB_0}|^2 $  
    →$ \{ (\vec{AB_0}･\vec{AB_1})^2 -2 (\vec{AB_0}･\vec{AB_1})^2 + |\vec{AB_0}|^2 |\vec{AB_1}|^2  \} t^2  
      + \{ -2 r |\vec{AB_0}| \cos \theta (\vec{AB_0}･\vec{AB_1}) +2 r |\vec{AB_0}| \cos \theta (\vec{AB_0}･\vec{AB_1}) \} t  
      + ( r^2 |\vec{AB_0}|^2 \cos^2 \theta - r^2 |\vec{AB_0}|^2 ) = 0 $  
    →$ \{ |\vec{AB_0}|^2 |\vec{AB_1}|^2 - (\vec{AB_0}･\vec{AB_1})^2 \} t^2 = r^2 |\vec{AB_0}|^2 \sin^2 \theta $  
    → $ t^2 = \dfrac{ r^2 |\vec{AB_0}|^2 \sin^2 \theta }{ |\vec{AB_0}|^2 |\vec{AB_1}|^2 - (\vec{AB_0}･\vec{AB_1})^2 }$  
    → $ t = \pm \dfrac{ r |\vec{AB_0}| \sin \theta }{ \sqrt{ |\vec{AB_0}|^2 |\vec{AB_1}|^2 - (\vec{AB_0}･\vec{AB_1})^2 } } \qquad (4) $  
    

- 式$(4)$から$t$を、式$(3)$から$s$を算出し、式$(1)$より点$P$を求めるが、式$(4)$で$t$は正負で$2$値あることから、点$P$も$2$点求まる。これは平面上で$\vec{AB_0}$を挟んで対称となる$2$点となっており、角度 $\theta$ の向きにあわせて$1$点を採用する。具体には、外積 $\vec{AB_0} \times \vec{AP}$ 、$\vec{AB_0} \times \vec{AB_1}$ の内積をとり、正値となる方(ベクトルの向きが同方向)の点$P$を採る。


In [10]:
import numpy as np

""" 任意の平面上でPointAから半径r、角度θの位置にある点の座標を計算する方法 """
def calc_point_from_radius_and_angle(PointA, PointB, RR, Theta):
    
    TT = [0 for i in range(2)]
    SS = [0 for i in range(2)]  
    VectorAB = [ calc_sum_vector(PointB[0], 1, PointA, -1), calc_sum_vector(PointB[1], 1, PointA, -1) ]
    ScalarAB = [ calc_mag_vector(VectorAB[0]), calc_mag_vector(VectorAB[1])
                , calc_scalar_product(VectorAB[0], VectorAB[1]) ]
        # ScalarAB[0] = calc_mag_vector(VectorAB[0])   # ベクトルA→B[0]の大きさ
        # ScalarAB[1] = calc_mag_vector(VectorAB[1])   # ベクトルA→B[1]の大きさ    
        # ScalarAB[2] = calc_scalar_product(VectorAB[0], VectorAB[1])   # ベクトルA→B[0]とA→B[0]の内積 
  
    TT[0] = ( RR * ScalarAB[0] * np.sin(Theta) ) \
          / ( ScalarAB[0]**2 * ScalarAB[1]**2 - ScalarAB[2]**2 )**0.5    # 正のt ← 式(4)
    TT[1] = - TT[0]    # 負のt ← 式(4)
    SS[0] = ( RR * ScalarAB[0] * np.cos(Theta) - TT[0] * ScalarAB[2] ) \
          /   ScalarAB[0]**2    # 正のtに対応するs ← 式(3)
    SS[1] = ( RR * ScalarAB[0] * np.cos(Theta) - TT[1] * ScalarAB[2] ) \
          /   ScalarAB[0]**2    # 負のtに対応するs ← 式(3)    
    VectorAP = [ calc_sum_vector(VectorAB[0], SS[0], VectorAB[1], TT[0])
               , calc_sum_vector(VectorAB[0], SS[1], VectorAB[1], TT[1]) ]   # ← 式(1) 
    
    ScalarC = calc_scalar_product( calc_vector_product(VectorAB[0], VectorAP[0])
                                 , calc_vector_product(VectorAB[0], VectorAB[1]) )
    if ScalarC > 0:
        PointP = calc_sum_vector(PointA, 1, VectorAP[0], 1)
    else:
        PointP = calc_sum_vector(PointA, 1, VectorAP[1], 1)        

    return PointP


In [11]:
""" calc_point_from_radius_and_angle - Test """

PointA = [0,0,0]
PointB = [[1,1,0],[-1,1,0],[-1,-1,0],[1,-1,0]]
RR = 2**0.5 / 2
Theta = np.radians(60)
PointP = calc_point_from_radius_and_angle(PointA, PointB, RR, Theta)
print(PointP)

[-0.18301270189221924, 0.68301270189221941, 0.0]



### C.2 多角形内に点を均等にばらまく方法

1) 山田俊雄「一様ランダム分布乱数点の凸型領域内への散布法」  
　https://www.jstage.jst.go.jp/article/geoinformatics1990/7/4/7_4_303/_pdf
  - 多角形内の一様なばらまき方について参考にした。
  
  
2) 渡辺宙志「一様乱数を使う」  
　http://apollon.issp.u-tokyo.ac.jp/~watanabe/pdf/prob.pdf
  - 円内の一様なばらまき方について参考にした。
  


以下、計算方法

- $N$角形の平面の式：$ax+by+cz=d$
- $N$角形の頂点の座標：$(x_0, y_0, z_0)$, $(x_1, y_1, z_1)$, …, $(x_{N-1}, y_{N-1}, z_{N-1})$
- 重心(らしき)点$A$の座標$(x_a, y_a, z_a)$を、各頂点の平均値から求める ← ここでは厳密に重心となる必要は無い
- 点$A$と各頂点の距離の最大値を、半径$R$とする。点$A$を中心とした$N$角形の平面上の半径$R$の円は、$N$角形を包含する。
- 包含する円内に均一に点をばらまく(上記文献$2$を参考に)  
  → 多角形内に「落ちた」もののみを「多角形内の始点」として扱う(上記文献$1$参考)。    
  → `NNN`は、多角形内に「落としたい」数  
  → 円内に「落とす」数は多角形と円の面積の比(と安全率)を考慮して割り増す → `NNN0`
- $0～1$の乱数 $rand$ を、`NNN0`組×各$2$個を生成する。
  - 再現性担保のため、乱数生成のシード `np.random.seed` は、`ini(R×10000)` としている。  
    → 生成される乱数を「同じもの」とするため。
  - $1$組目で、半径方向のばらまき: $r = \sqrt{rand} \times R = |\vec{AP}|$
  - $2$組目で、角度方向のばらまき: $\theta = rand \times 2 \pi$
  - 角度 $\theta$ の起点は点$A$から頂点$0$へのベクトルとする → $\vec{A0}=(x_0-x_a, y_0-y_a, z_0-z_a)$  
    → 頂点$1$から頂点$N$の方向に $\theta$ をまわすこととする。
    
    
- `NNN0`組の乱数について、`calc_point_from_radius_and_angle` で、円内にランダムに落ちる点の座標を計算
- 多角形の中に落ちているかどうかを `inside_or_not` で計算し、入っている場合にカウントアップ＆座標のリスト化
- 多角形内の数と円内の数の比で簡便に多角形の面積を計算可。ただし、数を増やさないとそれなりの精度にならないので、多角形の面積を計算するだけなら、`calc_area_of_polygon` を使用した方がよい。

In [12]:
import numpy as np

""" 平面上の多角形内に乱数を使って均等に点をばらまく """
def monte_carlo_in_polygon(NNN, PointB):
    # PointB: N角形の頂点の座標 → PointB[0], PointB[1], …, PointB[N-1]
    # PointB[i]の座標は → PointB[i][0], PointB[i][1], PointB[i][2]
    # NNN: N角形内で目標とする始点数
    # RationEx: 飛ばす数の安全率
    
    RationEx =1.0

    Plane_Eq = calc_plane_eq(PointB[0], PointB[1], PointB[2])    # 多角形のある平面の方程式
    Area = calc_area_of_polygon(PointB)    # 多角形の面積[m2]
    
    PointBt = list(map(list, zip(*PointB)))
    # zip関数でリストを転置→https://qiita.com/mas9612/items/821fbb4c881b7a836451
    
    # 重心(らしき)座標
    PointA = [ sum(PointBt[0])/len(PointBt[0]), sum(PointBt[1])/len(PointBt[1]), sum(PointBt[2])/len(PointBt[2]) ]
    
    # 重心(らしき)座標から頂点までの距離の最大値を取得 → 多角形平面上に多角形を包含する円を描く
    Radius = 0
    for i in range(len(PointB)):
        Length = calc_mag_vector(calc_sum_vector(PointB[i], 1, PointA, -1))
        if Length > Radius:
            Radius = Length    # 重心(らしき)座標を中心とした多角形を包含する円の半径
    CArea = np.pi * Radius**2  # 円の面積πr^2
    NNN0 = int( ( CArea / Area ) * NNN * RationEx + 1 ) 
        # 的を外す分の数に応じて面積比(と安全率)で飛ばす数を補正
   
    np.random.seed(int(Radius*10000) )
    Rand = np.random.rand(NNN0,2)   # 0〜1の乱数を NNN0×2 個生成

    PointPin = []
    NCircle = 0
    NPolygon = 0
    for i in range(NNN0):
        NCircle += 1    # 円内に落とした数総計
        RR = Rand[i,0]**0.5 * Radius    # 重心(らしき)座標からの距離r = (0～1の乱数)^0.5 * 半径Radius
        Theta = Rand[i,1] * 2 * np.pi   # 回転角θ[rad] = (0～1の乱数) * 2π 
        PointP = calc_point_from_radius_and_angle(PointA, PointB, RR, Theta)  # 円内で落ちる位置を計算
        [inside, ScalarC_pm] = inside_or_not(PointP, PointB)    # 多角形の中に落ちているかどうかを判定
        if inside == True:    # 多角形の中に落ちていれは、カウント
            NPolygon += 1
            PointPin.append( PointP )    # 入った座標リスト

    return [NCircle, NPolygon, CArea, Area, PointPin ]


In [13]:
""" monte_carlo_in_polygon - Test """

PointB = [[1,1,0],[-1,1,0],[-1,-1,-2],[1,-1,-2]]
NNN=100
[NCircle, NPolygon, CArea, Area, PointPin ] = monte_carlo_in_polygon(NNN,PointB)
print('試行回数 = {}: 多角形内落下数 = {}, 面積比 = {}, 円面積 = {}, 多角形面積 = {}, 面積比 = {} '
          .format( NCircle, NPolygon, NPolygon/NCircle, CArea, Area, Area/CArea ))
for i in range(NPolygon):
    print(PointPin[i])

試行回数 = 167: 多角形内落下数 = 108, 面積比 = 0.6467065868263473, 円面積 = 9.424777960769378, 多角形面積 = 5.656854249492381, 面積比 = 0.6002108774380709 
[-0.52894780231725036, -0.24280378327223839, -1.2428037832722385]
[-0.93766565654035916, 0.61918276498170655, -0.38081723501829345]
[-0.93905428536474966, -0.11152450743898501, -1.111524507438985]
[-0.06883382859194459, 0.36691578882834502, -0.63308421117165503]
[-0.72941497282906442, 0.39342151038489459, -0.60657848961510541]
[0.28296389559431662, 0.52253064484290812, -0.47746935515709188]
[0.82998843642305131, 0.8329369933364742, -0.1670630066635258]
[0.091852125683450914, 0.51308432475140342, -0.48691567524859658]
[-0.43307053160686027, 0.1444081561309479, -0.85559184386905207]
[0.48728750358518452, 0.81421177134186373, -0.18578822865813627]
[-0.50275313585459069, 0.40484520737334628, -0.59515479262665372]
[-0.69592315726795506, -0.28799316462216729, -1.2879931646221672]
[-0.60853838624959822, 0.45412154164162388, -0.54587845835837612]
[-0.99887808239187

### C.3 半球面を均等面積で小さい歪みで分割する方法
 
1) 渡辺宙志「一様乱数を使う」  
　http://apollon.issp.u-tokyo.ac.jp/~watanabe/pdf/prob.pdf
  - 球内の均等な面積割りの方法として参考にした。


以下、計算方法

- 全球を$N \times N$で分割する。半球で考えて$N \times N/2$分割。

- 上記文献より、単位球を極座標$(\theta, \phi)$としたときに、$z = \cos \theta$と変数変換することで、$z$、$\phi$で均等分割すればよいことになる($z=-1～1$、$\phi=0～2\pi$)。このときの座標は、下式の通り。
$$
\left\{
\begin{array}{ll}
x = \sqrt{ 1 - z^2 } \cos \phi \\
y = \sqrt{ 1 - z^2 } \sin \phi \\
z = z
\end{array}
\right.  
$$


- 半球を$y>0$側とし、$z$軸$+$側が天頂を、$z$軸$-$側が天底を指し、$y$軸$+$側を表面の法線ベクトルの向きとする。$z$軸に垂直な平面上における角度は、$x$軸$+$側が$- \pi / 2 [rad]$、$y$軸$+$側が$0 [rad]$、$x$軸$-$側が$ \pi / 2 [rad]$とする。


- 領域分割を半球の$1/4$の八分球$(x \geq 0, y \geq 0, z \geq 0)$で考えることとする。八分球を$(N/2)\times (N/4)$で分割する。


- 八分球で考えると、$z=0～1$。この範囲を$N/2$分割で等分する。分割幅は$\Delta z = 2 /N$。

- $\phi$は、$z$軸に垂直な平面上における角度。八分球で考えると $\phi=0～\pi/2$ の範囲となり、この範囲を$N/4$分割する。  
  → $N/4$分割した際の角度幅は、$\Delta \phi = (\pi/2) \big/(N/4)$。
- 縦方向の分割 $\Delta z$ と、横方向の分割 $\Delta \phi$ でできる球面上の領域の表面積 $S_{\Delta z \Delta \phi}$ は、 $S_{\Delta z \Delta \phi} = (\pi/2) \big/ (N/4) \times \Delta z$ となり、この方法で八分球を均等な面積で分割していることになる。
  
  
- 縦方向のある分割幅 $\Delta z_n$ における縦方向の円弧の長さ $l_{\Delta z_n} = \Delta \theta_n = \cos^{-1} z_{n-1} - \cos^{-1} z_{n}$。
- $z$軸に垂直な平面と半球でできる半円の半径は $\sqrt{ 1 - z^2 }$。縦方向のある分割幅 $\Delta z_n$ の中間高さにおける $\phi$ 方向の一分割あたりの円弧の長さは $l_{\Delta \phi} = (\pi/2) \sqrt{ 1 - \{(z_{n-1}+z_{n})/2\}^2 } \big/ (N/4)$。
- 縦横比を $l_{\Delta z_n} \; \big/ \; l_{\Delta \phi}$ で定義すると、赤道付近では横長の分割になる$(l_{\Delta z_n} \; \big/ \; l_{\Delta \phi} \simeq 0.318 )$。天頂付近では、$l_{\Delta z_n} \; \big/ \; l_{\Delta \phi} \gg 1$ となり、縦長の分割となる。  
→この比率が$1$に近づくように組み替えることを考える。


- 八分球を$(N/2)\times (N/4)$分割している各分割を、さらに $(N/4)\times (N/4)$ 分割する(細分割)。結局、八分球は $(N^2/8)\times (N^2/16)$ 分割。  
  → この細分割はすべて面積が同じ。  
  → 縦の分割$\times$横の分割が、$(N/4)\times (N/4)$ 個をみたしつつ、縦横比が$1$に近くなるように、縦、横の分割数を調整する。  
  → 横方向の分割数を $(N/4)\times (N/4)$の約数とすることで、八分球の平面方向の角度$90°$をぴったり均等に割ることができる。  
  → 最終的に、八分球は、それぞれが $(N/4)\times (N/4)$ の細分割をもつ、縦横の歪みが小さく調整され、表面積が均等な、$(N/2)\times (N/4)$ 個の分割に区切られる。

In [6]:
import numpy as np

""" ある数の約数の「小さい方半分」を降順で求める """
def calc_divisors_rh(MM):
    # 約数の小さい方半分を降順でを求める
    
    divisors_rh = [1]
    for i in range(2, int(MM**0.5) + 1):
        if MM % i == 0:
            divisors_rh.append(i)
            # if i != MM/i:             
            #    divisors.append(MM/i)  # 左の2行のコメントを外すと「大きい方半分」も求まる
    divisors_rh.reverse()               # 左のコメントを外すと降順で並び替え
    # divisors_rh.sort()                # 左のコメントを外すと昇順で並び替え
    
    return divisors_rh

In [7]:
MM = 60**2
divisors_rh = calc_divisors_rh(MM)
print(divisors_rh)

[60, 50, 48, 45, 40, 36, 30, 25, 24, 20, 18, 16, 15, 12, 10, 9, 8, 6, 5, 4, 3, 2, 1]


In [8]:
import numpy as np

""" 球面分割の面積算定 """
def calc_area_div_sphere(NNphi, delta_z):
    # delta_z: Δz。z軸方向の幅
    # NNphi: 八分球の水平方向の角度90°を何分割するか
    
    area_div_sphere = (np.pi/2) / NNphi * abs(delta_z)
    
    return area_div_sphere


""" 水平方向の円弧の長さ """
def calc_dphi(NNphi, zz):
    # zz: 円弧が載っている水平面のz座標(z = -1 ～ 1)
    # NNphi: 八分球の水平方向の角度90°を何分割するか
    
    dphi = (np.pi/2) * ( 1 - zz**2 )**0.5 / NNphi
    
    return dphi


In [47]:
import numpy as np
import sys

""" 八分球を表面積均等、歪み小さめで(NN**2/8)分割 """
def division_of_sphere(NN):
    # 全球をNN×NNで均等に分割
    # 半球の分割でいいので、NN×NN/2分割
    # ここでは、領域分割を半球の1/4の八分球(x≧0, y≧0, z≧0)で考えることとし、八分球を(NN/2)×(NN/4)で分割する
    
    if NN % 4 != 0:
        sys.exit("NNは4の倍数とする必要があります")         
    
    # 縦方向(θ方向)がNN/2分割。水平方向(φ方向)がNN/4分割
    # 各分割の中を(NN/4)×(NN/4)でさらに分割 → 縦横比を計算し、面積が同じで歪みの少ない分割に調整する。
    # 細分割は縦方向(θ方向)にNN**2/8分割。横方向(φ方向)にNN**2/16分割
    
    NNtheta0 = NN/2                # 縦方向(θ方向)がNN/2分割
    NNphi0   = NN/4                # 水平方向(φ方向)がNN/4分割
    NNrediv  = NN/4                # 各分割の中の再分割数→縦横ともに(NN/4)分割
    NNtheta1 = NNtheta0 * NNrediv  # 縦方向(θ方向)の細分割数が(NN/2)×(NN/4)分割
    NNphi1   = NNphi0 * NNrediv    # 水平方向(φ方向)の細分割数が(NN/4)×(NN/4)分割    

    divisors_rh = calc_divisors_rh(NNrediv**2)    # 約数の小さい方半分を降順で
    
    m = 0              # 分割の総数確認用
    div_sphere = [[0,0,0]]    #
    n0 = 0             # 縦方向分割下端(z=0側)の細分割の順番の初期設定  
    while m < NNtheta0 * NNphi0:
        for ii in range(len(divisors_rh)):
            if NNtheta0 * NNphi0 - m >= divisors_rh[ii]:
                dntheta0 = divisors_rh[ii]    # 縦方向分割数の初期設定
                i_divisors_rh = ii + 1
                break
        
        dnphi0 = NNrediv**2 / dntheta0
        n1 = n0 + dntheta0     # 縦方向分割上端(z=1側)の細分割の順番の初期設定
        z0 = n0 / NNtheta1
        z1 = n1 / NNtheta1       
        dtheta0 = abs( np.arccos(z0) - np.arccos(z1) )
        dphi0 = calc_dphi( NNphi1 / dnphi0, (z0 + z1)/2 )
        aratio0 =  dtheta0 / dphi0
        
        for i in range(i_divisors_rh, len(divisors_rh)):
            if aratio0 < 1: # 最初が横長.or.天頂付近で残りの縦方向分割に制限がある
                            #  or i_divisors_rh != 1
                dnphi = divisors_rh[i] 
                dntheta = NNrediv**2 / dnphi
            elif aratio0 > 1:                     # 最初が縦長
                dntheta = divisors_rh[i]                 
                dnphi = NNrediv**2 / dntheta
            else:
                break
                
            n1 = n0 + dntheta     # 縦方向分割上端(z=1側)の細分割の順番リセット
            z1 = n1 / NNtheta1                
            dtheta = abs( np.arccos(z0) - np.arccos(z1) )    
            dphi = calc_dphi( NNphi1 / dnphi, (z0 + z1)/2 )
            aratio =  dtheta / dphi

            if aratio0 <= 1 <= aratio:
                if aratio0 < 1/aratio <= 1:
                    dntheta0 = dntheta
                    dnphi0   = dnphi
                    aratio0  = aratio
                break
            elif aratio <= 1 <= aratio0:
                if 1/aratio0 < aratio <= 1:
                    dntheta0 = dntheta
                    dnphi0   = dnphi
                    aratio0  = aratio                    
                break
            else:
                dntheta0 = dntheta
                dnphi0   = dnphi
                aratio0  = aratio
                
        # 歪みが小さい分割要素の決定
        n1 = n0 + dntheta0     # 縦方向分割上端(z=1側)の細分割の順番
        z1 = n1 / NNtheta1
        h0 = np.pi/2 - np.arccos( z0 )    # 縦方向の角度を水平面からの見上げの角度hで収納する
        h1 = np.pi/2 - np.arccos( z1 )        
        hc = np.pi/2 - np.arccos( (z0+z1)/2 )
        dtheta0 = abs( np.arccos(z0) - np.arccos(z1) )
        dphi0 = calc_dphi( NNphi1 / dnphi0, (z0 + z1)/2 )
        aratio0 =  dtheta0 / dphi0
        NNphi2 = int(NNphi1 / dnphi0 + 0.1)    # 歪みを少なくすることで更新された水平方向の分割数
        area0 = calc_area_div_sphere(NNphi2, z1 - z0)

        div_sphere0 = []
        div_sphere0.append([h0,hc,h1])   
        for i in range(1,NNphi2+1):
            phi0 = (np.pi / 2) * (i-1) / NNphi2
            phi1 = (np.pi / 2) * i / NNphi2
            phic = (np.pi / 2) * (i-0.5) / NNphi2
            
            # 確認用
            # print(m+i,h0,hc,h1,phi0,phic,phi1,dntheta0,dnphi0,dtheta0,dphi0,aratio0,area0)
            
            div_sphere0.append([phi0,phic,phi1])
        div_sphere.append(div_sphere0)

        m += NNphi2        
        n0 = n1    # 縦方向分割下端(z=0側)の細分割の順番を更新 
        
    return div_sphere
    # div_sphere[i][j] → i: 水平方向の帯の層番号。i=1は水平面(hh=0)直上の層。i=Niが天頂(hh=π/2)を含む層
    #                  → j: 水平方向の層における方位角AA=0側からの分割番号。j=1がAA=0を含む分割。
    #                        j=NjがAA=π/2を含む分割
    # div_sphere[i][0]は、層iの仰角情報のリスト[下端のhh, 中央のhh, 上端のhh]
    # div_sphere[i][1]～[i][Nj]は、層iのj番目の分割の方位角情報のリスト[AA=0側のAA, 中央のAA, AA=π/2側のAA]


In [46]:
""" division_of_sphere - Test """
NN=240                         # 最終的には八分球をNN**2/8分割する。
div_sphere = division_of_sphere(NN)

NNtheta0 = NN/2                # 縦方向(θ方向)がNN/2分割
NNphi0   = NN/4                # 水平方向(φ方向)がNN/4分割
NNrediv  = NN/4                # 各分割の中の再分割数→縦横ともに(NN/4)分割
NNtheta1 = NNtheta0 * NNrediv  # 縦方向(θ方向)の細分割数が(NN/2)×(NN/4)分割
NNphi1   = NNphi0 * NNrediv    # 水平方向(φ方向)の細分割数が(NN/4)×(NN/4)分割   

m = 0
for i in range(1,len(div_sphere)):
    [h0,hc,h1] = div_sphere[i][0]
    dtheta0 = abs(h1-h0)
    z0 = np.cos(np.pi/2 - h0)
    z1 = np.cos(np.pi/2 - h1)
    dntheta0 = abs(z1-z0)*NNtheta1
   
    for j in range(1,len(div_sphere[i])):
        m += 1
        [phi0,phic,phi1] = div_sphere[i][j]
        dnphi0 = NNrediv**2 / (int((np.pi/2) / abs(phi1-phi0) + 0.1))
        dphi0 = calc_dphi( NNphi1 / dnphi0, (z0 + z1)/2 ) 
        aratio0 = dtheta0 / dphi0
        NNphi2 = int(NNphi1 / dnphi0 + 0.1)
        area0 = calc_area_div_sphere(NNphi2, abs(z1 - z0))
        print(m,h0,hc,h1,phi0,phic,phi1,dntheta0,dnphi0,dtheta0,dphi0,aratio0,area0)        

# print(div_sphere)

1 0.0 0.00694450026199 0.0138893354583 0.0 0.007853981633974483 0.015707963267948967 100.0 36 0.0138893354583 0.01570758450269403 0.884243879503 0.0002181661564992912
2 0.0 0.00694450026199 0.0138893354583 0.015707963267948967 0.023561944901923447 0.031415926535897934 100.0 36 0.0138893354583 0.01570758450269403 0.884243879503 0.0002181661564992912
3 0.0 0.00694450026199 0.0138893354583 0.031415926535897934 0.039269908169872414 0.047123889803846894 100.0 36 0.0138893354583 0.01570758450269403 0.884243879503 0.0002181661564992912
4 0.0 0.00694450026199 0.0138893354583 0.047123889803846894 0.05497787143782138 0.06283185307179587 100.0 36 0.0138893354583 0.01570758450269403 0.884243879503 0.0002181661564992912
5 0.0 0.00694450026199 0.0138893354583 0.06283185307179587 0.07068583470577035 0.07853981633974483 100.0 36 0.0138893354583 0.01570758450269403 0.884243879503 0.0002181661564992912
6 0.0 0.00694450026199 0.0138893354583 0.07853981633974483 0.08639379797371931 0.09424777960769379 100

102 0.0138893354583 0.0208348406686 0.0277813512638 0.015707963267948967 0.023561944901923447 0.031415926535897934 100.0 36 0.0138920158055 0.015704554051789887 0.884585182087 0.0002181661564992912
103 0.0138893354583 0.0208348406686 0.0277813512638 0.031415926535897934 0.039269908169872414 0.047123889803846894 100.0 36 0.0138920158055 0.015704554051789887 0.884585182087 0.0002181661564992912
104 0.0138893354583 0.0208348406686 0.0277813512638 0.047123889803846894 0.05497787143782138 0.06283185307179587 100.0 36 0.0138920158055 0.015704554051789887 0.884585182087 0.0002181661564992912
105 0.0138893354583 0.0208348406686 0.0277813512638 0.06283185307179587 0.07068583470577035 0.07853981633974483 100.0 36 0.0138920158055 0.015704554051789887 0.884585182087 0.0002181661564992912
106 0.0138893354583 0.0208348406686 0.0277813512638 0.07853981633974483 0.08639379797371931 0.09424777960769379 100.0 36 0.0138920158055 0.015704554051789887 0.884585182087 0.0002181661564992912
107 0.013889335458

298 0.0277813512638 0.0347292030514 0.0416787324226 1.5236724369910497 1.5315264186250241 1.5393804002589986 100.0 36 0.0138973811588 0.0156984913949788 0.885268578306 0.0002181661564992912
299 0.0277813512638 0.0347292030514 0.0416787324226 1.5393804002589986 1.547234381892973 1.5550883635269477 100.0 36 0.0138973811588 0.0156984913949788 0.885268578306 0.0002181661564992912
300 0.0277813512638 0.0347292030514 0.0416787324226 1.5550883635269477 1.5629423451609221 1.5707963267948966 100.0 36 0.0138973811588 0.0156984913949788 0.885268578306 0.0002181661564992912
301 0.0416787324226 0.048630276499 0.0555841732809 0.0 0.007853981633974483 0.015707963267948967 100.0 36 0.0139054408583 0.01568939301716843 0.886295654849 0.0002181661564992912
302 0.0416787324226 0.048630276499 0.0555841732809 0.015707963267948967 0.023561944901923447 0.031415926535897934 100.0 36 0.0139054408583 0.01568939301716843 0.886295654849 0.0002181661564992912
303 0.0416787324226 0.048630276499 0.0555841732809 0.031

538 0.0695003822519 0.0764633761834 0.0834300866106 0.5811946409141118 0.5890486225480862 0.5969026041820606 100.0 36 0.0139297043587 0.015662066171295005 0.889391233975 0.0002181661564992911
539 0.0695003822519 0.0764633761834 0.0834300866106 0.5969026041820606 0.6047565858160352 0.6126105674500096 100.0 36 0.0139297043587 0.015662066171295005 0.889391233975 0.0002181661564992911
540 0.0695003822519 0.0764633761834 0.0834300866106 0.6126105674500096 0.6204645490839842 0.6283185307179586 100.0 36 0.0139297043587 0.015662066171295005 0.889391233975 0.0002181661564992911
541 0.0695003822519 0.0764633761834 0.0834300866106 0.6283185307179586 0.6361725123519331 0.6440264939859075 100.0 36 0.0139297043587 0.015662066171295005 0.889391233975 0.0002181661564992911
542 0.0695003822519 0.0764633761834 0.0834300866106 0.6440264939859075 0.6518804756198822 0.6597344572538566 100.0 36 0.0139297043587 0.015662066171295005 0.889391233975 0.0002181661564992911
543 0.0695003822519 0.0764633761834 0.08

762 0.0973760373811 0.104355972588 0.111341014341 0.9581857593448869 0.9660397409788614 0.9738937226128358 100.0 36 0.0139649769598 0.015622509673101177 0.893900996195 0.0002181661564992911
763 0.0973760373811 0.104355972588 0.111341014341 0.9738937226128358 0.9817477042468102 0.9896016858807849 100.0 36 0.0139649769598 0.015622509673101177 0.893900996195 0.0002181661564992911
764 0.0973760373811 0.104355972588 0.111341014341 0.9896016858807849 0.9974556675147593 1.0053096491487339 100.0 36 0.0139649769598 0.015622509673101177 0.893900996195 0.0002181661564992911
765 0.0973760373811 0.104355972588 0.111341014341 1.0053096491487339 1.0131636307827083 1.0210176124166828 100.0 36 0.0139649769598 0.015622509673101177 0.893900996195 0.0002181661564992911
766 0.0973760373811 0.104355972588 0.111341014341 1.0210176124166828 1.0288715940506572 1.0367255756846319 100.0 36 0.0139649769598 0.015622509673101177 0.893900996195 0.0002181661564992911
767 0.0973760373811 0.104355972588 0.111341014341 

...

6219 1.0379976893 1.04487364078 1.05183202767 0.5026548245743669 0.5183627878423159 0.5340707511102649 50.0 72.0 0.0138343383641 0.0157711474038 0.877192889644 0.000218166156499
6220 1.0379976893 1.04487364078 1.05183202767 0.5340707511102649 0.5497787143782138 0.5654866776461628 50.0 72.0 0.0138343383641 0.0157711474038 0.877192889644 0.000218166156499
6221 1.0379976893 1.04487364078 1.05183202767 0.5654866776461628 0.5811946409141118 0.5969026041820606 50.0 72.0 0.0138343383641 0.0157711474038 0.877192889644 0.000218166156499
6222 1.0379976893 1.04487364078 1.05183202767 0.5969026041820606 0.6126105674500096 0.6283185307179586 50.0 72.0 0.0138343383641 0.0157711474038 0.877192889644 0.000218166156499
6223 1.0379976893 1.04487364078 1.05183202767 0.6283185307179586 0.6440264939859075 0.6597344572538566 50.0 72.0 0.0138343383641 0.0157711474038 0.877192889644 0.000218166156499
6224 1.0379976893 1.04487364078 1.05183202767 0.6597344572538566 0.6754424205218055 0.6911503837897545 50.0 72

6438 1.09552077332 1.10285778661 1.11030290174 1.1453723216212788 1.1617347833587257 1.1780972450961724 48.0 75.0 0.0147821284112 0.0147604913929 1.00146587385 0.000218166156499
6439 1.09552077332 1.10285778661 1.11030290174 1.1780972450961724 1.1944597068336191 1.210822168571066 48.0 75.0 0.0147821284112 0.0147604913929 1.00146587385 0.000218166156499
6440 1.09552077332 1.10285778661 1.11030290174 1.210822168571066 1.227184630308513 1.2435470920459597 48.0 75.0 0.0147821284112 0.0147604913929 1.00146587385 0.000218166156499
6441 1.09552077332 1.10285778661 1.11030290174 1.2435470920459597 1.2599095537834066 1.2762720155208533 48.0 75.0 0.0147821284112 0.0147604913929 1.00146587385 0.000218166156499
6442 1.09552077332 1.10285778661 1.11030290174 1.2762720155208533 1.2926344772583003 1.3089969389957472 48.0 75.0 0.0147821284112 0.0147604913929 1.00146587385 0.000218166156499
6443 1.09552077332 1.10285778661 1.11030290174 1.3089969389957472 1.325359400733194 1.3417218624706406 48.0 75.0 

6667 1.16950038081 1.176672408 1.18397031126 1.4922565104551517 1.511891464540088 1.5315264186250241 40.0 90.0 0.0144699304583 0.0150796220116 0.959568512205 0.000218166156499
6668 1.16950038081 1.176672408 1.18397031126 1.5315264186250241 1.5511613727099605 1.5707963267948966 40.0 90.0 0.0144699304583 0.0150796220116 0.959568512205 0.000218166156499
6669 1.18397031126 1.19140137107 1.19897358784 0.0 0.019634954084936207 0.039269908169872414 40.0 90.0 0.0150032765797 0.0145439450047 1.03158232342 0.000218166156499
6670 1.18397031126 1.19140137107 1.19897358784 0.039269908169872414 0.05890486225480862 0.07853981633974483 40.0 90.0 0.0150032765797 0.0145439450047 1.03158232342 0.000218166156499
6671 1.18397031126 1.19140137107 1.19897358784 0.07853981633974483 0.09817477042468103 0.11780972450961724 40.0 90.0 0.0150032765797 0.0145439450047 1.03158232342 0.000218166156499
6672 1.18397031126 1.19140137107 1.19897358784 0.11780972450961724 0.13744467859455345 0.15707963267948966 40.0 90.0 

6876 1.25861758689 1.26547363246 1.27248217434 1.2042771838760873 1.2304571226560024 1.2566370614359172 30.0 120.0 0.0138645874575 0.0157394294902 0.880882465665 0.000218166156499
6877 1.25861758689 1.26547363246 1.27248217434 1.2566370614359172 1.2828170002158321 1.3089969389957472 30.0 120.0 0.0138645874575 0.0157394294902 0.880882465665 0.000218166156499
6878 1.25861758689 1.26547363246 1.27248217434 1.3089969389957472 1.335176877775662 1.3613568165555772 30.0 120.0 0.0138645874575 0.0157394294902 0.880882465665 0.000218166156499
6879 1.25861758689 1.26547363246 1.27248217434 1.3613568165555772 1.387536755335492 1.413716694115407 30.0 120.0 0.0138645874575 0.0157394294902 0.880882465665 0.000218166156499
6880 1.25861758689 1.26547363246 1.27248217434 1.413716694115407 1.439896632895322 1.4660765716752369 30.0 120.0 0.0138645874575 0.0157394294902 0.880882465665 0.000218166156499
6881 1.25861758689 1.26547363246 1.27248217434 1.4660765716752369 1.4922565104551517 1.5184364492350668 3

7102 1.39182748648 1.39899127048 1.40646384979 1.3962634015954636 1.439896632895322 1.4835298641951802 18.0 200.0 0.014636363308 0.0149191711803 0.981043995745 0.000218166156499
7103 1.39182748648 1.39899127048 1.40646384979 1.4835298641951802 1.5271630954950384 1.5707963267948966 18.0 200.0 0.014636363308 0.0149191711803 0.981043995745 0.000218166156499
7104 1.40646384979 1.41340089123 1.42065534464 0.0 0.04908738521234052 0.09817477042468103 16.0 225.0 0.0141914948563 0.015388539092 0.922211963819 0.000218166156499
7105 1.40646384979 1.41340089123 1.42065534464 0.09817477042468103 0.14726215563702155 0.19634954084936207 16.0 225.0 0.0141914948563 0.015388539092 0.922211963819 0.000218166156499
7106 1.40646384979 1.41340089123 1.42065534464 0.19634954084936207 0.2454369260617026 0.2945243112740431 16.0 225.0 0.0141914948563 0.015388539092 0.922211963819 0.000218166156499
7107 1.40646384979 1.41340089123 1.42065534464 0.2945243112740431 0.3436116964863836 0.39269908169872414 16.0 225.0

### C.4 表面上の点から半球に(構造的に)投射して衝突するオブジェクトを確認する方法

In [ ]:
""" 表面上の点から半球に(構造的に)投射して衝突するオブジェクトを確認する方法 """
def collision_ps():
    # 始点IDリスト: startID
    # 衝突判定するIDリスト: endID
    # オブジェクトの座標リスト: Point[ID]
    # NN: 全球の分割数がNN**2
    # NStart: 始点IDのオブジェクト内から放射する始点の数。NStart=1だと代表点1点からの放射
    
    # 八分球を表面積均等、歪み小さめで(NN**2/8)分割
    NN=240                         # 最終的には八分球をNN**2/8分割する。
    div_sphere = division_of_sphere(NN)    
    # div_sphere[i][j] → i: 水平方向の帯の層番号。i=1は水平面(hh=0)直上の層。i=Niが天頂(hh=π/2)を含む層
    #                  → j: 水平方向の層における方位角AA=0側からの分割番号。j=1がAA=0を含む分割。
    #                        j=NjがAA=π/2を含む分割
    # div_sphere[i][0]は、層iの仰角情報のリスト[下端のhh, 中央のhh, 上端のhh]
    # div_sphere[i][1]～[i][Nj]は、層iのj番目の分割の方位角情報のリスト[AA=0側のAA, 中央のAA, AA=π/2側のAA]
   
    
    # 始点となるオブジェクトのループ
    for ssid in startID:
        if NStart > 1:
            [NCircle, NPolygon, CArea, Area, ssp0 ] = monte_carlo_in_polygon(NStart,Point[ssid])
        else:
            ssp0 = [ CenterP[ssid] ]
        
        # 始点のループ
        for ssp in ssp0:
            
    
    
    
    
    return angle_and_obj
    
    
    

In [55]:
import numpy as np
import sys

""" 球面の仰角(高度)と方位角から属する分割の座標を引っこ抜く """
def division_from_div_sphere(div_sphere,hh,AA):
    # hh: 仰角[rad], 正値は太陽高度。負値は地面方向
    # AA: 始点となる物理オブジェクト(窓とか)基準の方位角。法線ベクトルが0radで
    #    「窓」から見て右手が正、左手が負の角度
    # div_sphere: division_of_sphere で区分した八分球(x>0,y>0)の分割の座標
    # div_sphere[i][j] → i: 水平方向の帯の層番号。i=1は水平面(hh=0)直上の層。i=Niが天頂(hh=π/2)を含む層
    #                  → j: 水平方向の層における方位角AA=0側からの分割番号。j=1がAA=0を含む分割。
    #                        j=NjがAA=π/2を含む分割
    # div_sphere[i][0]は、層iの仰角情報のリスト[下端のhh, 中央のhh, 上端のhh]
    # div_sphere[i][1]～[i][Nj]は、層iのj番目の分割の方位角情報のリスト[AA=0側のAA, 中央のhh, AA=π/2側のAA]
    
    division = []
    division_i = []
    division_j = []
    for i in range(1,len(div_sphere)):
        if div_sphere[i][0][0] <= abs(hh) <= div_sphere[i][0][2]:
            if hh >= 0:
                division_i = div_sphere[i][0]
            else:
                division_i = [-div_sphere[i][0][0],-div_sphere[i][0][1],-div_sphere[i][0][2]]             
                i = -i
            break
    for j in range(1,len(div_sphere[i])):
        if div_sphere[i][j][0] <= abs(AA) <= div_sphere[i][j][2]:
            if AA >= 0:
                division_j = div_sphere[i][j]                
            else:
                division_j = [-div_sphere[i][j][0],-div_sphere[i][j][1],-div_sphere[i][j][2]]  
                j = -j
            break                
  
    division = [i,j]
    division.append(division_i)
    division.append(division_j)    
    
    return division


In [56]:
""" division_from_div_sphere - Test """

NN=240
div_sphere = division_of_sphere(NN)

for Nhh in range(-90, 91):
    hh = (np.pi/2) * Nhh / 90
    for NAA in range(-90, 91):
        AA =(np.pi/2) * NAA / 90
        division = division_from_div_sphere(div_sphere,hh,AA)
        print (hh,AA,division)
        
        

-1.5707963267948966 -1.5707963267948966 [-107, -100, [-1.5541294672209656, -1.5590111455731686, -1.5707963267948966], [-1.5550883635269477, -1.5629423451609221, -1.5707963267948966]]
-1.5707963267948966 -1.5533430342749535 [-107, -99, [-1.5541294672209656, -1.5590111455731686, -1.5707963267948966], [-1.5393804002589986, -1.547234381892973, -1.5550883635269477]]
-1.5707963267948966 -1.53588974175501 [-107, -98, [-1.5541294672209656, -1.5590111455731686, -1.5707963267948966], [-1.5236724369910497, -1.5315264186250241, -1.5393804002589986]]
-1.5707963267948966 -1.5184364492350666 [-107, -97, [-1.5541294672209656, -1.5590111455731686, -1.5707963267948966], [-1.5079644737231006, -1.515818455357075, -1.5236724369910497]]
-1.5707963267948966 -1.5009831567151233 [-107, -96, [-1.5541294672209656, -1.5590111455731686, -1.5707963267948966], [-1.4922565104551517, -1.5001104920891262, -1.5079644737231006]]
-1.5707963267948966 -1.4835298641951802 [-107, -95, [-1.5541294672209656, -1.5590111455731686

-1.5533430342749535 1.1519173063162575 [-106, 74, [-1.5419278108972181, -1.5472255551141556, -1.5541294672209656], [1.1466813185602744, 1.154535300194249, 1.1623892818282235]]
-1.5533430342749535 1.1693705988362006 [-106, 75, [-1.5419278108972181, -1.5472255551141556, -1.5541294672209656], [1.1623892818282235, 1.170243263462198, 1.1780972450961724]]
-1.5533430342749535 1.1868238913561442 [-106, 76, [-1.5419278108972181, -1.5472255551141556, -1.5541294672209656], [1.1780972450961724, 1.1859512267301469, 1.1938052083641213]]
-1.5533430342749535 1.2042771838760873 [-106, 77, [-1.5419278108972181, -1.5472255551141556, -1.5541294672209656], [1.1938052083641213, 1.201659189998096, 1.2095131716320704]]
-1.5533430342749535 1.2217304763960306 [-106, 78, [-1.5419278108972181, -1.5472255551141556, -1.5541294672209656], [1.2095131716320704, 1.2173671532660448, 1.2252211349000193]]
-1.5533430342749535 1.239183768915974 [-106, 79, [-1.5419278108972181, -1.5472255551141556, -1.5541294672209656], [1.2

-1.4835298641951802 1.3962634015954636 [-102, 89, [-1.4810134273322078, -1.488277124824378, -1.496243463141536], [1.382300767579509, 1.3901547492134836, 1.398008730847458]]
-1.4835298641951802 1.413716694115407 [-102, 90, [-1.4810134273322078, -1.488277124824378, -1.496243463141536], [1.398008730847458, 1.4058627124814325, 1.413716694115407]]
-1.4835298641951802 1.43116998663535 [-102, 92, [-1.4810134273322078, -1.488277124824378, -1.496243463141536], [1.4294246573833558, 1.4372786390173302, 1.4451326206513047]]
-1.4835298641951802 1.4486232791552935 [-102, 93, [-1.4810134273322078, -1.488277124824378, -1.496243463141536], [1.4451326206513047, 1.4529866022852793, 1.4608405839192538]]
-1.4835298641951802 1.4660765716752369 [-102, 94, [-1.4810134273322078, -1.488277124824378, -1.496243463141536], [1.4608405839192538, 1.4686945655532284, 1.4765485471872029]]
-1.4835298641951802 1.4835298641951802 [-102, 95, [-1.4810134273322078, -1.488277124824378, -1.496243463141536], [1.4765485471872029

-1.3962634015954636 0.9948376736367678 [-96, 64, [-1.3918274864771523, -1.3989912704775918, -1.4064638497851198], [0.9896016858807849, 0.9974556675147593, 1.0053096491487339]]
-1.3962634015954636 1.0122909661567112 [-96, 65, [-1.3918274864771523, -1.3989912704775918, -1.4064638497851198], [1.0053096491487339, 1.0131636307827083, 1.0210176124166828]]
-1.3962634015954636 1.0297442586766543 [-96, 66, [-1.3918274864771523, -1.3989912704775918, -1.4064638497851198], [1.0210176124166828, 1.0288715940506572, 1.0367255756846319]]
-1.3962634015954636 1.0471975511965976 [-96, 67, [-1.3918274864771523, -1.3989912704775918, -1.4064638497851198], [1.0367255756846319, 1.0445795573186063, 1.0524335389525807]]
-1.3962634015954636 1.064650843716541 [-96, 68, [-1.3918274864771523, -1.3989912704775918, -1.4064638497851198], [1.0524335389525807, 1.0602875205865552, 1.0681415022205298]]
-1.3962634015954636 1.0821041362364843 [-96, 69, [-1.3918274864771523, -1.3989912704775918, -1.4064638497851198], [1.0681

-1.3089969389957472 0.4537856055185257 [-90, 29, [-1.3022841045272471, -1.3102523915200746, -1.3184662963107532], [0.43982297150257105, 0.4476769531365455, 0.45553093477052004]]
-1.3089969389957472 0.47123889803846897 [-90, 31, [-1.3022841045272471, -1.3102523915200746, -1.3184662963107532], [0.4712388980384689, 0.47909287967244346, 0.4869468613064179]]
-1.3089969389957472 0.4886921905584123 [-90, 32, [-1.3022841045272471, -1.3102523915200746, -1.3184662963107532], [0.4869468613064179, 0.49480084294039245, 0.5026548245743669]]
-1.3089969389957472 0.5061454830783556 [-90, 33, [-1.3022841045272471, -1.3102523915200746, -1.3184662963107532], [0.5026548245743669, 0.5105088062083414, 0.5183627878423159]]
-1.3089969389957472 0.5235987755982988 [-90, 34, [-1.3022841045272471, -1.3102523915200746, -1.3184662963107532], [0.5183627878423159, 0.5262167694762904, 0.5340707511102649]]
-1.3089969389957472 0.5410520681182421 [-90, 35, [-1.3022841045272471, -1.3102523915200746, -1.3184662963107532], [

...

1.2217304763960306 0.3316125578789226 [84, 8, [1.2129880610073434, 1.2201959237759952, 1.2275487371438831], [0.30543261909900765, 0.32724923474893675, 0.3490658503988659]]
1.2217304763960306 0.3490658503988659 [84, 8, [1.2129880610073434, 1.2201959237759952, 1.2275487371438831], [0.30543261909900765, 0.32724923474893675, 0.3490658503988659]]
1.2217304763960306 0.3665191429188092 [84, 9, [1.2129880610073434, 1.2201959237759952, 1.2275487371438831], [0.3490658503988659, 0.37088246604879505, 0.39269908169872414]]
1.2217304763960306 0.3839724354387525 [84, 9, [1.2129880610073434, 1.2201959237759952, 1.2275487371438831], [0.3490658503988659, 0.37088246604879505, 0.39269908169872414]]
1.2217304763960306 0.40142572795869574 [84, 10, [1.2129880610073434, 1.2201959237759952, 1.2275487371438831], [0.39269908169872414, 0.41451569734865323, 0.4363323129985824]]
1.2217304763960306 0.41887902047863906 [84, 10, [1.2129880610073434, 1.2201959237759952, 1.2275487371438831], [0.39269908169872414, 0.4145

1.3089969389957472 0.3839724354387525 [90, 8, [1.3022841045272471, 1.3102523915200746, 1.3184662963107532], [0.3665191429188092, 0.3926990816987241, 0.41887902047863906]]
1.3089969389957472 0.40142572795869574 [90, 8, [1.3022841045272471, 1.3102523915200746, 1.3184662963107532], [0.3665191429188092, 0.3926990816987241, 0.41887902047863906]]
1.3089969389957472 0.41887902047863906 [90, 8, [1.3022841045272471, 1.3102523915200746, 1.3184662963107532], [0.3665191429188092, 0.3926990816987241, 0.41887902047863906]]
1.3089969389957472 0.4363323129985824 [90, 9, [1.3022841045272471, 1.3102523915200746, 1.3184662963107532], [0.41887902047863906, 0.44505895925855404, 0.47123889803846897]]
1.3089969389957472 0.4537856055185257 [90, 9, [1.3022841045272471, 1.3102523915200746, 1.3184662963107532], [0.41887902047863906, 0.44505895925855404, 0.47123889803846897]]
1.3089969389957472 0.47123889803846897 [90, 9, [1.3022841045272471, 1.3102523915200746, 1.3184662963107532], [0.41887902047863906, 0.445058

1.3962634015954636 -0.8377580409572781 [96, -10, [1.3918274864771523, 1.3989912704775918, 1.4064638497851198], [-0.7853981633974483, -0.8290313946973065, -0.8726646259971648]]
1.3962634015954636 -0.8203047484373349 [96, -10, [1.3918274864771523, 1.3989912704775918, 1.4064638497851198], [-0.7853981633974483, -0.8290313946973065, -0.8726646259971648]]
1.3962634015954636 -0.8028514559173915 [96, -10, [1.3918274864771523, 1.3989912704775918, 1.4064638497851198], [-0.7853981633974483, -0.8290313946973065, -0.8726646259971648]]
1.3962634015954636 -0.7853981633974483 [96, -9, [1.3918274864771523, 1.3989912704775918, 1.4064638497851198], [-0.6981317007977318, -0.7417649320975901, -0.7853981633974483]]
1.3962634015954636 -0.767944870877505 [96, -9, [1.3918274864771523, 1.3989912704775918, 1.4064638497851198], [-0.6981317007977318, -0.7417649320975901, -0.7853981633974483]]
1.3962634015954636 -0.7504915783575616 [96, -9, [1.3918274864771523, 1.3989912704775918, 1.4064638497851198], [-0.698131700

1.4660765716752369 0.8552113334772214 [100, 7, [1.4517021503352434, 1.4589346149430935, 1.4666659874246175], [0.7853981633974483, 0.8508480103472357, 0.916297857297023]]
1.4660765716752369 0.8726646259971648 [100, 7, [1.4517021503352434, 1.4589346149430935, 1.4666659874246175], [0.7853981633974483, 0.8508480103472357, 0.916297857297023]]
1.4660765716752369 0.890117918517108 [100, 7, [1.4517021503352434, 1.4589346149430935, 1.4666659874246175], [0.7853981633974483, 0.8508480103472357, 0.916297857297023]]
1.4660765716752369 0.9075712110370514 [100, 7, [1.4517021503352434, 1.4589346149430935, 1.4666659874246175], [0.7853981633974483, 0.8508480103472357, 0.916297857297023]]
1.4660765716752369 0.9250245035569946 [100, 8, [1.4517021503352434, 1.4589346149430935, 1.4666659874246175], [0.916297857297023, 0.9817477042468102, 1.0471975511965976]]
1.4660765716752369 0.9424777960769379 [100, 8, [1.4517021503352434, 1.4589346149430935, 1.4666659874246175], [0.916297857297023, 0.9817477042468102, 1.

1.5533430342749535 -0.3141592653589793 [106, -1, [1.5419278108972181, 1.5472255551141556, 1.5541294672209656], [-0.0, -0.39269908169872414, -0.7853981633974483]]
1.5533430342749535 -0.29670597283903605 [106, -1, [1.5419278108972181, 1.5472255551141556, 1.5541294672209656], [-0.0, -0.39269908169872414, -0.7853981633974483]]
1.5533430342749535 -0.2792526803190927 [106, -1, [1.5419278108972181, 1.5472255551141556, 1.5541294672209656], [-0.0, -0.39269908169872414, -0.7853981633974483]]
1.5533430342749535 -0.2617993877991494 [106, -1, [1.5419278108972181, 1.5472255551141556, 1.5541294672209656], [-0.0, -0.39269908169872414, -0.7853981633974483]]
1.5533430342749535 -0.24434609527920614 [106, -1, [1.5419278108972181, 1.5472255551141556, 1.5541294672209656], [-0.0, -0.39269908169872414, -0.7853981633974483]]
1.5533430342749535 -0.22689280275926285 [106, -1, [1.5419278108972181, 1.5472255551141556, 1.5541294672209656], [-0.0, -0.39269908169872414, -0.7853981633974483]]
1.5533430342749535 -0.209